In [1]:
import argparse
import os
import sys

sys.path.append(os.getcwd())

from dotenv import load_dotenv

load_dotenv("env/.env")

from dl_ba import common_utils
from balm.configs import Configs
from balm.trainer import Trainer


In [2]:
import os
import wandb
import numpy as np
import pandas as pd
import torch
from accelerate import Accelerator
from accelerate.tracking import WandBTracker
from datasets import Dataset
from tdc.multi_pred import DTI
from torch.nn import functional as F
from torch.optim import AdamW
from torch.utils.data import DataLoader
from tqdm import tqdm
from transformers import (
    AutoTokenizer,
    DefaultDataCollator,
    get_linear_schedule_with_warmup,
)

from balm.configs import Configs
from balm.dataset import PairedBindingDataset
from balm.metrics import get_ci, get_pearson, get_rmse, get_spearman
from balm.model import BindingAffinityModel
from balm.tokenization import pre_tokenize_unique_entities, tokenize_with_lookup


In [3]:


class Trainer:
    def __init__(self, configs: Configs, wandb_entity: str, wandb_project: str):
        self.configs = configs

        self.gradient_accumulation_steps = (
            self.configs.model_configs.model_hyperparameters.gradient_accumulation_steps
        )
        self.max_seq_len = self.configs.model_configs.model_hyperparameters.max_seq_len

        self.outputs_dir = self.configs.training_configs.outputs_dir
        self.wandb_entity = wandb_entity
        self.wandb_project = wandb_project

        self.protein_tokenizer, self.drug_tokenizer = self._load_tokenizers()
        self.model = BindingAffinityModel(self.configs.model_configs)

        (
            self.train_dataloader,
            self.valid_dataloader,
            self.test_dataloader,
        ) = self._load_dataset()

        self._setup_run_name()
        self._setup_training()

    def _load_tokenizers(self):
        protein_tokenizer = AutoTokenizer.from_pretrained(
            self.configs.model_configs.protein_model_name_or_path
        )
        drug_tokenizer = AutoTokenizer.from_pretrained(
            self.configs.model_configs.drug_model_name_or_path
        )

        return protein_tokenizer, drug_tokenizer

    def _load_dataset(self) -> dict:
        dataset = DTI(name=self.configs.dataset_configs.dataset_name)
        if self.configs.dataset_configs.harmonize_affinities_mode:
            dataset.harmonize_affinities(
                mode=self.configs.dataset_configs.harmonize_affinities_mode
            )
            # Convert $K_d$ to $pKd$
            dataset.convert_to_log(form="binding")

        # If the loss function is infonce, we need to do a binning
        # based on the selected threshold
        print(
            f"Training with {self.configs.model_configs.loss_function} loss function."
        )
        if self.configs.model_configs.loss_function in ["infonce"]:
            pkd_threshold = self.configs.model_configs.loss_hyperparameters[
                "pkd_threshold"
            ]
            dataset.y = [1 if pkd >= pkd_threshold else 0 for pkd in dataset.y]
        elif self.configs.model_configs.loss_function in ["cosine_mse"]:
            pkd_upper_bound = self.configs.model_configs.loss_hyperparameters[
                "pkd_upper_bound"
            ]
            print(f"Scaling labels by = {pkd_upper_bound}")
            dataset.y = [pkd / pkd_upper_bound for pkd in dataset.y]

        dataset_splits = {}
        for split, data_df in dataset.get_split().items():
            # Pre-tokenize unique ligands and proteins for this split
            print(f"Pre-tokenize unique ligands and proteins for {split}")
            protein_tokenized_dict, drug_tokenized_dict = pre_tokenize_unique_entities(
                data_df, self.protein_tokenizer, self.drug_tokenizer
            )

            if self.configs.model_configs.loss_function in ["infonce"]:
                self.num_negative_samples = (
                    self.configs.model_configs.loss_hyperparameters[
                        "num_negative_samples"
                    ]
                )
                self.query_entity_column = (
                    self.configs.model_configs.loss_hyperparameters[
                        "query_entity_column"
                    ]
                )

                dataset = PairedBindingDataset(
                    data_df,
                    protein_tokenized_dict,
                    drug_tokenized_dict,
                    self.num_negative_samples,
                    self.query_entity_column,
                )
            else:
                # Use the optimized tokenization for this split
                dataset = Dataset.from_pandas(data_df).map(
                    lambda x: tokenize_with_lookup(
                        x, protein_tokenized_dict, drug_tokenized_dict
                    ),
                )
            dataset_splits[split] = dataset

        data_collator = DefaultDataCollator(return_tensors="pt")

        print(f"Setup Train DataLoader")
        train_dataloader = DataLoader(
            dataset_splits["train"],
            shuffle=True,
            collate_fn=data_collator,
            batch_size=self.configs.training_configs.batch_size,
            pin_memory=True,
        )
        print(f"Setup Valid DataLoader")
        valid_dataloader = DataLoader(
            dataset_splits["valid"],
            shuffle=True,
            collate_fn=data_collator,
            batch_size=self.configs.training_configs.batch_size,
            pin_memory=True,
        )
        print(f"Setup Test DataLoader")
        test_dataloader = DataLoader(
            dataset_splits["test"],
            shuffle=True,
            collate_fn=data_collator,
            batch_size=self.configs.training_configs.batch_size,
            pin_memory=True,
        )

        return train_dataloader, valid_dataloader, test_dataloader

    def _setup_run_name(self):
        protein_peft_hyperparameters = (
            self.configs.model_configs.protein_peft_hyperparameters
        )
        drug_peft_hyperparameters = self.configs.model_configs.drug_peft_hyperparameters
        # Group name depends on the model in use and their tuning configuration
        ## Get model names
        protein_model_name = self.configs.model_configs.protein_model_name_or_path
        drug_model_name = self.configs.model_configs.drug_model_name_or_path

        ## Get model training methods
        protein_model_peft = "frozen"
        drug_model_peft = "frozen"
        if protein_peft_hyperparameters is not None:
            protein_model_peft = self.configs.model_configs.peft_type
        if drug_peft_hyperparameters is not None:
            drug_model_peft = self.configs.model_configs.peft_type

        ## Set group name
        self.group_name = f"{protein_model_name}_{protein_model_peft}__{drug_model_name}_{drug_model_peft}"

        # Run name depends on the hyperparameters
        ## Get hyperparameters
        hyperparams = []
        if protein_peft_hyperparameters:
            hyperparams += ["protein"]
            for key, value in protein_peft_hyperparameters.items():
                hyperparams += [f"{key}_{value}"]
        if drug_peft_hyperparameters:
            hyperparams += ["drug"]
            for key, value in drug_peft_hyperparameters.items():
                hyperparams += [f"{key}_{value}"]
        self.run_name = "_".join(hyperparams)

    def _setup_training(self):
        self.accelerator = Accelerator(
            gradient_accumulation_steps=self.gradient_accumulation_steps,
            log_with="wandb",
        )
        self.wandb_tracker = None
        if self.accelerator.is_main_process:
            self.accelerator.init_trackers(
                project_name=self.wandb_project,
                init_kwargs={
                    "wandb": {
                        "entity": self.wandb_entity,
                        "name": self.run_name,
                        "group": self.group_name,
                    }
                },
            )
            self.wandb_tracker: WandBTracker = self.accelerator.get_tracker("wandb")
        self.accelerator.wait_for_everyone()
        # self.wandb_tracker.init()

        # optimizer
        self.optimizer = AdamW(
            params=[param for param in self.model.parameters() if param.requires_grad],
            lr=self.configs.model_configs.model_hyperparameters.learning_rate,
        )

        # lr scheduler
        warmup_steps_ratio = (
            self.configs.model_configs.model_hyperparameters.warmup_steps_ratio
        )
        num_training_steps = (
            len(self.train_dataloader) * self.configs.training_configs.epochs
        )
        self.lr_scheduler = get_linear_schedule_with_warmup(
            optimizer=self.optimizer,
            num_warmup_steps=warmup_steps_ratio,
            num_training_steps=num_training_steps,
        )

        (
            self.model,
            self.train_dataloader,
            self.valid_dataloader,
            self.test_dataloader,
            self.optimizer,
            self.lr_scheduler,
        ) = self.accelerator.prepare(
            self.model,
            self.train_dataloader,
            self.valid_dataloader,
            self.test_dataloader,
            self.optimizer,
            self.lr_scheduler,
        )

    def compute_metrics(self, labels, predictions):
        if self.configs.model_configs.loss_function in ["cosine_mse"]:
            labels *= self.configs.model_configs.loss_hyperparameters["pkd_upper_bound"]
            predictions *= self.configs.model_configs.loss_hyperparameters[
                "pkd_upper_bound"
            ]
        rmse = get_rmse(labels, predictions)
        pearson = get_pearson(labels, predictions)
        spearman = get_spearman(labels, predictions)
        ci = get_ci(labels, predictions)

        return {
            "rmse": rmse,
            "pearson": pearson,
            "spearman": spearman,
            "ci": ci,
        }

    def train(self):
        for epoch in range(self.configs.training_configs.epochs):
            self.model.train()

            num_train_steps = len(self.train_dataloader)
            progress_bar = tqdm(
                total=num_train_steps,
                position=0,
                leave=True,
                disable=not self.accelerator.is_local_main_process,
            )
            prev_valid_loss = 100000
            for train_step, batch in enumerate(self.train_dataloader):
                with self.accelerator.accumulate(self.model):
                    kwargs = {}
                    if self.configs.model_configs.loss_function in ["infonce"]:
                        kwargs["query_entity"] = self.query_entity_column
                    if self.configs.model_configs.loss_function in ["cosine_mse"]:
                        kwargs["labels"] = batch["Y"]

                    outputs = self.model(batch, **kwargs)
                    loss = outputs["loss"]

                    # Backpropagate
                    self.accelerator.backward(loss)
                    self.optimizer.step()
                    self.lr_scheduler.step()
                    self.model.zero_grad()
                    self.optimizer.zero_grad()

                    progress_bar.set_description(f"Epoch {epoch}; Loss: {loss:.4f}")

                # Checks if the accelerator has performed an optimization step behind the scenes
                if self.accelerator.sync_gradients:
                    progress_bar.update(1)

            # At the end of an epoch, compute metrics
            train_metrics = self.test("train")
            valid_metrics = self.test("valid")
            self.accelerator.log(train_metrics | valid_metrics, step=epoch)
            # Save a checkpoint
            if valid_metrics["valid/loss"] < prev_valid_loss:
                prev_valid_loss = valid_metrics["valid/loss"]
                best_checkpoint_dir = f"step_{epoch}"
                self.accelerator.save_state(
                    os.path.join(self.outputs_dir, best_checkpoint_dir)
                )

        # Load best checkpoint for test evaluation
        self.accelerator.load_state(os.path.join(self.outputs_dir, best_checkpoint_dir))
        self.accelerator.wait_for_everyone()

        test_metrics = self.test("test")
        self.accelerator.log(test_metrics, step=epoch)

    def test(self, split: str):
        if split == "train":
            dataloader = self.train_dataloader
        elif split == "valid":
            dataloader = self.valid_dataloader
        elif split == "test":
            dataloader = self.test_dataloader

        total_loss = 0
        all_labels = []
        all_predictions = []

        self.model.eval()

        num_steps = len(dataloader)
        progress_bar = tqdm(
            total=num_steps,
            position=0,
            leave=True,
            disable=not self.accelerator.is_local_main_process,
        )
        for step, batch in enumerate(tqdm(dataloader)):
            kwargs = {}
            if self.configs.model_configs.loss_function in ["infonce"]:
                kwargs["query_entity"] = self.query_entity_column
            if self.configs.model_configs.loss_function in ["cosine_mse"]:
                kwargs["labels"] = batch["Y"]

            with torch.no_grad():
                outputs = self.model(batch, **kwargs)
                loss = outputs["loss"]
                total_loss += loss.detach().float()

                if self.configs.model_configs.loss_function in ["cosine_mse"]:
                    all_labels += [kwargs["labels"]]
                    all_predictions += [outputs["cosine_similarity"]]

            progress_bar.set_description(f"Eval {split}")
            progress_bar.update(1)

        all_labels = torch.cat(all_labels, dim=0)
        all_predictions = torch.cat(all_predictions, dim=0)
        performance_metrics = self.compute_metrics(all_labels, all_predictions)
        metrics = {
            f"{split}/loss": total_loss / len(dataloader),
        }
        for metric_name, metric_value in performance_metrics.items():
            metrics[f"{split}/{metric_name}"] = metric_value

        return metrics


In [4]:
configs = Configs(**common_utils.load_yaml('configs/experiments/esm_chemberta_lora_cosinemse.yaml'))

common_utils.setup_random_seed(configs.training_configs.random_seed)
outputs_dir = common_utils.setup_experiment_folder(
        os.path.join(os.getcwd(), configs.training_configs.outputs_dir)
    )
common_utils.save_training_configs(configs, outputs_dir)

# Login to WandB
wandb_api="40399e7dca359f27027ffe07c3da8c0a7f7af50c"
wandb_entity = "dlba"
wandb_project = "dlba_train"
wandb.login(key=wandb_api)
trainer = Trainer(configs, wandb_entity, wandb_project)

wandb: Currently logged in as: rohangorantla (dlba). Use `wandb login --relogin` to force relogin
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /home/co-gora1/.netrc
Some weights of EsmModel were not initialized from the model checkpoint at facebook/esm2_t30_150M_UR50D and are newly initialized: ['esm.pooler.dense.bias', 'esm.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaModel were not initialized from the model checkpoint at DeepChem/ChemBERTa-77M-MTR and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Fou

trainable params: 1,843,200 || all params: 150,638,681 || trainable%: 1.2235901083069096
trainable params: 110,592 || all params: 3,538,032 || trainable%: 3.1258055325672576


Done!
The scale is in original affinity scale, so we will take the minimum!
The original data has been updated!
To log space...


Training with cosine_mse loss function.
Scaling labels by = 10
Pre-tokenize unique ligands and proteins for train


Map:   0%|          | 0/29565 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/8447 [00:00<?, ? examples/s]

Detected kernel version 4.18.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


Setup Train DataLoader
Setup Valid DataLoader
Setup Test DataLoader


Error in callback <bound method _WandbInit._pause_backend of <wandb.sdk.wandb_init._WandbInit object at 0x7f710cb46050>> (for post_run_cell), with arguments args (<ExecutionResult object at 7f7113d3ec20, execution_count=4 error_before_exec=None error_in_exec=None info=<ExecutionInfo object at 7f7113d3f250, raw_cell="configs = Configs(**common_utils.load_yaml('config.." store_history=True silent=False shell_futures=True cell_id=None> result=None>,),kwargs {}:


TypeError: _WandbInit._pause_backend() takes 1 positional argument but 2 were given

In [ ]:
from accelerate import notebook_launcher

notebook_launcher(trainer.train(), mixed_precision="bf16")

Error in callback <bound method _WandbInit._resume_backend of <wandb.sdk.wandb_init._WandbInit object at 0x7f710cb46050>> (for pre_run_cell), with arguments args (<ExecutionInfo object at 7f7106e5f160, raw_cell="from accelerate import notebook_launcher

notebook.." store_history=True silent=False shell_futures=True cell_id=None>,),kwargs {}:


TypeError: _WandbInit._resume_backend() takes 1 positional argument but 2 were given

Eval train:  21%|██████                       | 193/924 [01:45<06:41,  1.82it/s]


Eval train:  42%|████████████▏                | 387/924 [03:55<04:55,  1.82it/s]


Eval train:  63%|██████████████████▏          | 581/924 [05:42<03:08,  1.82it/s]


...

Eval train:  39%|███████████▎                 | 361/924 [03:19<05:11,  1.81it/s]


Eval train:  60%|█████████████████▍           | 555/924 [05:06<03:23,  1.81it/s]


Eval train:  81%|███████████████████████▌     | 749/924 [06:53<01:37,  1.80it/s]


Eval valid:  12%|███▋                          | 16/132 [00:08<01:04,  1.81it/s]


Epoch 43; Loss: 0.0235:  13%|█▉             | 122/924 [10:56<1:11:44,  5.37s/it]